In [15]:
import gymnasium as gym
from pogema import GridConfig
from stable_baselines3 import DQN, A2C
from stable_baselines3.common.evaluation import evaluate_policy

%load_ext autoreload
%autoreload 2
%matplotlib inline

grid_config = GridConfig(
    size=8,
    density=0.3,
    num_agents=1,
    max_episode_steps=64
)

env = gym.make("Pogema-v0",grid_config=grid_config)

a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1
)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:29: UserWarning: WARN: It seems a Box observation space is an image but the `dtype` is not `np.uint8`, actual type: float32. If the Box observation space is not an image, we recommend flattening the observation to have only a 1D vector.
  logger.warn(
/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:34: UserWarning: WARN: It seems a Box observation space is an image but the lower and upper bounds are not [0, 255]. Actual lower bound: -1.0, upper bound: 1.0. Generally, CNN policies assume observations are within that range, so you may encounter an issue if the observation values are not.
  logger.warn(


#### Optuna Integration

In [16]:
""" Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using A2C implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python sb3_simple.py

"""
from typing import Any
from typing import Dict

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import A2C
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.monitor import Monitor
import torch
import torch.nn as nn


N_TRIALS = 100
N_STARTUP_TRIALS = 5
N_EVALUATIONS = 2
N_TIMESTEPS = int(5.0e5)
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 3


DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "verbose": 1,
    "env": env
}

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """Sampler for A2C hyperparameters."""
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)

    trial.set_user_attr("gamma", gamma)

    return {
        "gamma": gamma,
        "learning_rate": learning_rate,
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model.
    model = A2C(**kwargs)
    # Create env used for evaluation.
    eval_env = Monitor(env)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env, trial, n_eval_episodes=N_EVAL_EPISODES, eval_freq=EVAL_FREQ, deterministic=True
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3)

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, n_jobs=4, timeout=600)
    except KeyboardInterrupt:
        pass

    print("Number of finished trials: ", len(study.trials))

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print("    {}: {}".format(key, value))


[I 2023-11-10 16:32:44,209] A new study created in memory with name: no-name-3f346f77-fc71-46b3-a1fb-788fee438f8d
[W ParallelNative.cpp:230] Warning: Cannot set number of intraop threads after parallel work has started or after set_num_threads call when using native parallel backend (function set_num_threads)


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 55.2     |
|    ep_rew_mean        | 0.222    |
| time/                 |          |
|    fps                | 183      |
|    iterations         | 100      |
|    time_elapsed       | 2        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -1.48    |
|    explained_variance | -0.0772  |
|    learning_rate      | 0.000783 |
|    n_updates          | 99       |
|    policy_loss        | 0.00508  |
|    value_loss         | 0.000627 |
--------------------------------

[I 2023-11-10 17:17:45,078] Trial 1 finished with value: 0.0 and parameters: {'gamma': 0.09017504633047631, 'lr': 0.0007832178598290373}. Best is trial 1 with value: 0.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 40.9      |
|    ep_rew_mean        | 0.32      |
| time/                 |           |
|    fps                | 168       |
|    iterations         | 91000     |
|    time_elapsed       | 2700      |
|    total_timesteps    | 455000    |
| train/                |           |
|    entropy_loss       | -0.000409 |
|    explained_variance | 5.96e-08  |
|    learning_rate      | 0.000565  |
|    n_updates          | 90999     |
|    policy_loss        | -1.52e-08 |
|    value_loss         | 2.55e-07  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 53.6      |
|    ep_rew_mean        | 0.29      |
| time/                 |           |
|    fps                | 166       |
|    iterations         | 90100     |
|    time_elapsed       | 2701      |
|    total_timesteps    | 450500    |
| train/    

[I 2023-11-10 17:20:13,353] Trial 0 finished with value: 0.0 and parameters: {'gamma': 0.0005370993083536465, 'lr': 0.542815584792915}. Best is trial 1 with value: 0.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 48.2      |
|    ep_rew_mean        | 0.21      |
| time/                 |           |
|    fps                | 173       |
|    iterations         | 99000     |
|    time_elapsed       | 2849      |
|    total_timesteps    | 495000    |
| train/                |           |
|    entropy_loss       | -6.57e-05 |
|    explained_variance | 0         |
|    learning_rate      | 0.000565  |
|    n_updates          | 98999     |
|    policy_loss        | -1.32e-09 |
|    value_loss         | 9.35e-08  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 41.9      |
|    ep_rew_mean        | 0.36      |
| time/                 |           |
|    fps                | 172       |
|    iterations         | 98200     |
|    time_elapsed       | 2850      |
|    total_timesteps    | 491000    |
| train/    

[I 2023-11-10 17:20:24,546] Trial 3 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.00017402180228498335, 'lr': 0.0005645052291876103}. Best is trial 3 with value: 0.3333333333333333.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 55.7      |
|    ep_rew_mean        | 0.17      |
| time/                 |           |
|    fps                | 173       |
|    iterations         | 99200     |
|    time_elapsed       | 2860      |
|    total_timesteps    | 496000    |
| train/                |           |
|    entropy_loss       | -2.41e-05 |
|    explained_variance | 0         |
|    learning_rate      | 0.000793  |
|    n_updates          | 99199     |
|    policy_loss        | -1.5e-10  |
|    value_loss         | 7.58e-09  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 58.5      |
|    ep_rew_mean        | 0.15      |
| time/                 |           |
|    fps                | 173       |
|    iterations         | 99300     |
|    time_elapsed       | 2860      |
|    total_timesteps    | 496500    |
| train/    

[I 2023-11-10 17:20:27,518] Trial 2 finished with value: 0.0 and parameters: {'gamma': 0.005746069235524785, 'lr': 0.0007930038333011165}. Best is trial 3 with value: 0.3333333333333333.


Number of finished trials:  4
Best trial:
  Value:  0.3333333333333333
  Params: 
    gamma: 0.00017402180228498335
    lr: 0.0005645052291876103
  User attrs:
    gamma: 0.999825978197715


### Train agent with best hyper parameters

In [17]:
a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1,
    gamma=1-0.00017402180228498335,#0.05301162025483709,
    learning_rate=0.0005645052291876103#0.002305035463312779,
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [18]:
# Train agent and save it
a2c_model.learn(int(5.0e5))
a2c_model.save("saved/a2c_a")

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 43.4     |
|    ep_rew_mean        | 0.364    |
| time/                 |          |
|    fps                | 1650     |
|    iterations         | 100      |
|    time_elapsed       | 0        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -1.6     |
|    explained_variance | -2.68    |
|    learning_rate      | 0.000565 |
|    n_updates          | 99       |
|    policy_loss        | -0.00349 |
|    value_loss         | 8.74e-06 |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 49.5     |
|    ep_rew_mean        | 0.3      |
| time/                 |          |
|    fps                | 1516     |
|    iterations         | 200      |
|    time_elapsed       | 0        |
|    total_timesteps    | 1000     |
| train/                |          |
|

#### Testing 

In [19]:
a2c_model = A2C.load("saved/a2c_a")

env.reset()

mean_reward, std_reward = evaluate_policy(a2c_model, env, deterministic=True, n_eval_episodes=20)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

mean_reward:0.40 +/- 0.49


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


In [20]:
# RANDOM SEED
from IPython.display import SVG, display
from pogema.animation import AnimationMonitor, AnimationConfig

env = AnimationMonitor(env)

def evaluate_success_rate(model, env, num_episodes=1000):
    success_count = 0
    step_array = []
    for i in range(num_episodes):
        print(f'---{i}---')
        obs = env.reset()

        # Check if observation is a tuple and extract the first element if true.
        if isinstance(obs, tuple):
            obs = obs[0]
        max_step = 64
        steps_taken = 0
        done = truncated = False
        while not done and max_step > 0:
            action, _ = model.predict(obs)
            next_obs, reward, done, truncated, info = env.step(action)
            print(action,max_step,success_count,done)
            max_step -= 1
            steps_taken += 1
            # Check if next_obs is a tuple and extract the first element if true.
            if isinstance(next_obs, tuple):
                next_obs = next_obs[0]
            obs = next_obs

            # Check if agent was successful in that episode.
            if done:
                success_count += 1
                step_array.append(steps_taken)
                env.save_animation(f"render{i}.svg", AnimationConfig(egocentric_idx=0))
                break

    success_rate = success_count / num_episodes
    return success_rate, step_array

success_rate,step_array = evaluate_success_rate(a2c_model, env)
print(f"Agent Success Rate: {success_rate * 100:.2f}%")
print(f"steps to termination : {step_array}")

---0---
4 64 0 False
3 63 0 False
4 62 0 False
3 61 0 False
4 60 0 False
3 59 0 False
4 58 0 False
3 57 0 False
4 56 0 False
3 55 0 False
4 54 0 False
3 53 0 False
1 52 0 False
3 51 0 True
---1---
4 64 1 False
4 63 1 False
1 62 1 True
---2---
1 64 2 False
4 63 2 False
4 62 2 True
---3---
4 64 3 False
3 63 3 False
4 62 3 False
3 61 3 False
4 60 3 False
3 59 3 False
4 58 3 False
3 57 3 False
4 56 3 False
3 55 3 False
4 54 3 False
3 53 3 False
4 52 3 False
3 51 3 False
4 50 3 False
3 49 3 False
4 48 3 False
3 47 3 False
4 46 3 False
3 45 3 False
4 44 3 False
3 43 3 False
4 42 3 False
3 41 3 False
4 40 3 False
3 39 3 False
4 38 3 False
3 37 3 False
4 36 3 False
3 35 3 False
4 34 3 False
3 33 3 False
4 32 3 False
3 31 3 False
4 30 3 False
3 29 3 False
4 28 3 False
3 27 3 False
4 26 3 False
3 25 3 False
4 24 3 False
3 23 3 False
4 22 3 False
3 21 3 False
4 20 3 False
3 19 3 False
4 18 3 False
3 17 3 False
4 16 3 False
3 15 3 False
4 14 3 False
3 13 3 False
4 12 3 False
3 11 3 False
4 10 3 Fa

In [21]:
step_array

[14,
 3,
 3,
 6,
 9,
 2,
 1,
 2,
 2,
 1,
 4,
 2,
 5,
 8,
 1,
 7,
 59,
 48,
 4,
 3,
 1,
 17,
 3,
 8,
 4,
 3,
 20,
 1,
 1,
 1,
 22,
 5,
 35,
 4,
 3,
 1,
 3,
 7,
 3,
 5,
 4,
 8,
 13,
 18,
 6,
 2,
 5,
 1,
 3,
 2,
 4,
 1,
 1,
 5,
 5,
 1,
 1,
 1,
 2,
 10,
 4,
 4,
 2,
 1,
 23,
 49,
 18,
 13,
 37,
 1,
 1,
 1,
 5,
 1,
 1,
 7,
 13,
 6,
 1,
 1,
 6,
 30,
 4,
 9,
 6,
 39,
 5,
 3,
 29,
 2,
 8,
 1,
 36,
 1,
 7,
 2,
 12,
 6,
 26,
 8,
 3,
 21,
 4,
 16,
 2,
 6,
 2,
 2,
 3,
 3,
 8,
 3,
 3,
 7,
 4,
 11,
 5,
 44,
 4,
 2,
 34,
 2,
 33,
 1,
 2,
 8,
 26,
 46,
 1,
 3,
 12,
 1,
 5,
 49,
 2,
 3,
 1,
 4,
 3,
 2,
 5,
 28,
 11,
 7,
 9,
 17,
 1,
 2,
 32,
 14,
 35,
 7,
 1,
 7,
 3,
 28,
 3,
 2,
 3,
 28,
 10,
 2,
 1,
 20,
 24,
 3,
 5,
 2,
 29,
 4,
 24,
 13,
 3,
 3,
 3,
 1,
 46,
 5,
 7,
 1,
 2,
 2,
 3,
 2,
 14,
 1,
 3,
 1,
 1,
 44,
 1,
 55,
 2,
 2,
 1,
 5,
 13,
 4,
 3,
 2,
 5,
 10,
 6,
 2,
 3,
 17,
 9,
 40,
 1,
 40,
 1,
 8,
 48,
 16,
 46,
 27,
 1,
 3,
 2,
 6,
 11,
 7,
 1,
 15,
 4,
 1,
 12,
 48,
 2,
 6,
 26,
 4,
 6,
 28,

In [22]:
import numpy as np
np.mean(step_array)

9.558712121212121